<a href="https://colab.research.google.com/github/Gabrieldiasdeoliveira/Analise_Performance_Comercial/blob/main/Analise_Performance_Comercial.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Para esse teste a equipe de Data & Analytics da Vivaz criou uma métrica chamada Score.
Essa variável atribui pontos a atividades relevantes para a equipe de vendas. Você deverá considerar para o score TODAS as atividades listadas no arquivo Score Atividades, onde você também encontrará a pontuação de cada uma delas.


# Objetivo

1. *Ranking Vendedor – Classificação de todos os vendedores do score mais alto para o mais baixo. Será considerado diferencial a aplicação de uma análise de curva ABC que demonstre o número e quem são os vendedores que deverão receber bônus e o número e quem são os vendedores que irão para o comitê de baixa performance.*

2. *Ranking Coordenador – Classificação de todos os coordenadores, através da composição do score de sua equipe.* **Dica: Se atente para a diferença no número de vendedores das equipes. Não realize apenas a soma do score dos vendedores.**
3. *Ranking Gerente – Para esse Ranking, queremos testar não apenas sua capacidade técnica, mas também sua percepção sobre como medir a performance de um gerente.* **Dica: Vendedores que não vendem com regularidade (pelo menos 1 venda por mês) são muito prejudiciais para a empresa.**

In [55]:
library(readxl)
library(dplyr)
library(ggplot2)
library(stringr)
library(tidyr)
library(knitr)

In [47]:
# Leitura dos dados
atividades1 <- read_xlsx ("/Atividades - Missão corporativa.xlsx")
equipes <- read_xlsx ("/Equipes - Missão corporativa.xlsx")
score <- read_xlsx ("/Score Atividades - Missão corporativa.xlsx")
vendas <- read_xlsx ("/Vendas - Missão corporativa.xlsx")

# Nessa etapa, vamos entender a estrutura das nossas bases e realizar um processo de ETL antes de prosseguir com o objetivo. Pode ser que haja alguma análise descritiva, mas apenas para facilitar o processo de ETL.

In [56]:
head(atividades1)

Mês contabil Carimbo de data/hora Vendedores Nome Vendedores SobrenNome
1 2020-01-01   2020-02-04 15:02:26  Aarão           Barrios              
2 2020-01-01   2020-02-04 13:51:33  Abílio          Canhão               
3 2020-01-01   2020-02-04 13:50:47  Alicia          Félix                
4 2020-01-01   2020-02-04 12:17:56  Alicia          Severiano            
5 2020-01-01   2020-02-04 12:08:06  Angélica        Rangel               
6 2020-01-01   2020-02-04 12:02:11  Baltasar        Colaço               
  Atividade
1  7       
2 10       
3 10       
4  8       
5  2       
6  8

In [57]:
# Separando data e hora na base de dados
atividades <- separate(atividades1, col = "Carimbo de data/hora", into = c("Carimbo de Data", "Hora Carimbo"), sep = " ")

In [58]:
# Supondo que a base de dados "atividades" já esteja carregada, vamos criar a nova variável "Nome Vendedor" juntando as duas variáveis existentes
atividades <- atividades %>%
  mutate(`Nome Vendedor` = paste(`Vendedores Nome`, `Vendedores SobrenNome`, sep = " "))


# Agora que criamos a nova variável, podemos remover as variáveis originais, se necessário
atividades <- atividades %>%
  select(-`Vendedores Nome`, -`Vendedores SobrenNome`)

In [59]:
# Visualizando a base
head(atividades)

Mês contabil Carimbo de Data Hora Carimbo Atividade Nome Vendedor   
1 2020-01-01   2020-02-04      15:02:26      7        Aarão Barrios   
2 2020-01-01   2020-02-04      13:51:33     10        Abílio Canhão   
3 2020-01-01   2020-02-04      13:50:47     10        Alicia Félix    
4 2020-01-01   2020-02-04      12:17:56      8        Alicia Severiano
5 2020-01-01   2020-02-04      12:08:06      2        Angélica Rangel 
6 2020-01-01   2020-02-04      12:02:11      8        Baltasar Colaço

In [60]:
dim(atividades)     # Retorna o número de linhas e colunas da base de atividades

[1] 1237    5

In [61]:
# Visualizando a base
head(equipes)

Código Vendedor         Coordenador       Gerente       
1 1      Aarão Barrios    Anacleto Parreira Oriana Camargo
2 2      Abílio Canhão    Anacleto Parreira Oriana Camargo
3 3      Alicia Félix     Anacleto Parreira Oriana Camargo
4 4      Alicia Severiano Augusto Conde     Oriana Camargo
5 5      Angélica Rangel  Augusto Conde     Oriana Camargo
6 6      Baltasar Colaço  Catarino Veiga    Oriana Camargo

In [62]:
# Exibe a estrutura da base de equipes
str(equipes)

tibble [59 × 4] (S3: tbl_df/tbl/data.frame)
 $ Código     : num [1:59] 1 2 3 4 5 6 7 8 9 10 ...
 $ Vendedor   : chr [1:59] "Aarão Barrios" "Abílio Canhão" "Alicia Félix" "Alicia Severiano" ...
 $ Coordenador: chr [1:59] "Anacleto Parreira" "Anacleto Parreira" "Anacleto Parreira" "Augusto Conde" ...
 $ Gerente    : chr [1:59] "Oriana Camargo" "Oriana Camargo" "Oriana Camargo" "Oriana Camargo" ...


In [63]:
# Visualizando a base
print(score)

# A tibble: 15 × 4
   Classificação   Atividade         `Código Atividade`  Score
   <chr>           <chr>                          <dbl>  <dbl>
 1 Início do funil Visita Indicação                   1   10  
 2 Início do funil Retorno                            2    3  
 3 Início do funil Ponto Externo                      3    1  
 4 Início do funil Trabalho na Rua                    4    1  
 5 Início do funil Oferta Ativa                       5    0.1
 6 Início do funil Carteira Corretor                  6    1  
 7 Lead Recebido   Espontânea                         7  -10  
 8 Lead Recebido   Whatsapp                           8   -1  
 9 Lead Recebido   E-mail                             9   -1  
10 Lead Recebido   Chat                              10   -1  
11 Meio do Funil   Clientes Perdidos                 11  -10  
12 Meio do Funil   Pastas iniciadas                  12   10  
13 Meio do Funil   Siqac rodado                      13  100  
14 Meio do Funil   Venda Estoque    

In [64]:
dim(score)

[1] 15  4

In [65]:
summary(score$Score)      # Resumo estatístico da base de score

   Min. 1st Qu.  Median    Mean 3rd Qu.    Max. 
  -10.0    -1.0     1.0   126.9    10.0  1000.0 

In [66]:
score <- score %>%
  rename(`Nome Atividade` = Atividade)

In [67]:
head(vendas)

REGIONAL CODIGO OBRA CODIGOBLOCO NOME BLOCO UNIDADE VENDEDOR           
1 VIVAZ SP 3131        01          TORRE 01   000003  Odilia Maciel      
2 VIVAZ SP 3131        01          TORRE 01   000009  Vivaldo Cachoeira  
3 VIVAZ SP 3131        01          TORRE 01   000101  Enia Alburquerque  
4 VIVAZ SP 3131        01          TORRE 01   000103  Gisela Martínez    
5 VIVAZ SP 3131        01          TORRE 01   000104  Abílio Canhão      
6 VIVAZ SP 3131        01          TORRE 01   000105  Quintiliano Moreyra
  EMPRESA DE VENDAS MES CONTABIL DATA DE CONTABILIZAÇÃO DO SAP TIPO            
1 VIVAZ VENDAS      9/2020       2020-09-24 15:27:03           Venda Lançamento
2 VIVAZ VENDAS      9/2020       2020-09-24 14:51:56           Venda Lançamento
3 VIVAZ VENDAS      9/2020       2020-10-01 15:53:01           Venda Lançamento
4 VIVAZ VENDAS      9/2020       2020-10-01 16:52:39           Venda Lançamento
5 VIVAZ VENDAS      10/2020      2020-10-23 05:57:41           Venda Lançamento
6 VIVAZ VENDAS      9/2020       2020-09-24 06:47:27           Venda Lançamento
  TIPO VENDA RAZAO STATUS           
1 Nova Venda AG - Suporte Financeiro
2 Nova Venda AG - Suporte Financeiro
3 Nova Venda AG - Suporte Financeiro
4 Nova Venda AG - Suporte Financeiro
5 Nova Venda AS - Assinada          
6 Nova Venda AS - Assinada

*Convertendo as variáveis em letra minúscula.*

In [68]:
# Vetor com os nomes originais das colunas
nomes_originais <- c("REGIONAL", "CODIGO OBRA", "CODIGOBLOCO", "NOME BLOCO", "UNIDADE", "VENDEDOR", "EMPRESA DE VENDAS", "MES CONTABIL", "DATA DE CONTABILIZAÇÃO DO SAP", "TIPO", "TIPO VENDA", "RAZAO STATUS")

# Converter os nomes para letras minúsculas
nomes_minusculos <- tolower(nomes_originais)

# Atribuir os novos nomes à base de vendas
colnames(vendas) <- nomes_minusculos

# Visualizar os novos nomes das colunas na base de vendas
colnames(vendas)

[1] "regional"                      "codigo obra"                  
 [3] "codigobloco"                   "nome bloco"                   
 [5] "unidade"                       "vendedor"                     
 [7] "empresa de vendas"             "mes contabil"                 
 [9] "data de contabilização do sap" "tipo"                         
[11] "tipo venda"                    "razao status"

In [69]:
# Visualiza as primeiras linhas da base de vendas
head(vendas)

regional codigo obra codigobloco nome bloco unidade vendedor           
1 VIVAZ SP 3131        01          TORRE 01   000003  Odilia Maciel      
2 VIVAZ SP 3131        01          TORRE 01   000009  Vivaldo Cachoeira  
3 VIVAZ SP 3131        01          TORRE 01   000101  Enia Alburquerque  
4 VIVAZ SP 3131        01          TORRE 01   000103  Gisela Martínez    
5 VIVAZ SP 3131        01          TORRE 01   000104  Abílio Canhão      
6 VIVAZ SP 3131        01          TORRE 01   000105  Quintiliano Moreyra
  empresa de vendas mes contabil data de contabilização do sap tipo            
1 VIVAZ VENDAS      9/2020       2020-09-24 15:27:03           Venda Lançamento
2 VIVAZ VENDAS      9/2020       2020-09-24 14:51:56           Venda Lançamento
3 VIVAZ VENDAS      9/2020       2020-10-01 15:53:01           Venda Lançamento
4 VIVAZ VENDAS      9/2020       2020-10-01 16:52:39           Venda Lançamento
5 VIVAZ VENDAS      10/2020      2020-10-23 05:57:41           Venda Lançamento
6 VIVAZ VENDAS      9/2020       2020-09-24 06:47:27           Venda Lançamento
  tipo venda razao status           
1 Nova Venda AG - Suporte Financeiro
2 Nova Venda AG - Suporte Financeiro
3 Nova Venda AG - Suporte Financeiro
4 Nova Venda AG - Suporte Financeiro
5 Nova Venda AS - Assinada          
6 Nova Venda AS - Assinada

In [70]:
# Retorna o número de linhas e colunas da base de atividades
dim(vendas)

[1] 2858   12

*Nessa etapa, percebemos que, devido à variável "Código Atividade" da base "score" e à variável "Atividade" da base "Atividades", conseguimos realizar um left_join para unir as duas tabelas.*


In [71]:
head(score)
head(atividades)

Classificação   Nome Atividade    Código Atividade Score
1 Início do funil Visita Indicação  1                10.0 
2 Início do funil Retorno           2                 3.0 
3 Início do funil Ponto Externo     3                 1.0 
4 Início do funil Trabalho na Rua   4                 1.0 
5 Início do funil Oferta Ativa      5                 0.1 
6 Início do funil Carteira Corretor 6                 1.0

Mês contabil Carimbo de Data Hora Carimbo Atividade Nome Vendedor   
1 2020-01-01   2020-02-04      15:02:26      7        Aarão Barrios   
2 2020-01-01   2020-02-04      13:51:33     10        Abílio Canhão   
3 2020-01-01   2020-02-04      13:50:47     10        Alicia Félix    
4 2020-01-01   2020-02-04      12:17:56      8        Alicia Severiano
5 2020-01-01   2020-02-04      12:08:06      2        Angélica Rangel 
6 2020-01-01   2020-02-04      12:02:11      8        Baltasar Colaço

In [72]:
# Fazendo o join usando a função left_join do dplyr
result <- left_join(atividades, score, by = c("Atividade" = "Código Atividade"))

In [73]:
# Remover as colunas que não vamos precisar no momento
result <- result %>%
  select(-`Mês contabil`, -`Carimbo de Data`, -`Hora Carimbo`)

In [74]:
head(result)

Atividade Nome Vendedor    Classificação   Nome Atividade Score
1  7        Aarão Barrios    Lead Recebido   Espontânea     -10  
2 10        Abílio Canhão    Lead Recebido   Chat            -1  
3 10        Alicia Félix     Lead Recebido   Chat            -1  
4  8        Alicia Severiano Lead Recebido   Whatsapp        -1  
5  2        Angélica Rangel  Início do funil Retorno          3  
6  8        Baltasar Colaço  Lead Recebido   Whatsapp        -1

In [75]:
# Vamos classificar os vendedores com base no score
resultado_classificado <- result %>%
  arrange(desc(Score)) %>%
  group_by(`Nome Vendedor`) %>%
  mutate(Classificacao = row_number())

# Mostrando o resultado da classificação
head(resultado_classificado)

Atividade Nome Vendedor     Classificação Nome Atividade Score Classificacao
1 13        Elias Morera      Meio do Funil Siqac rodado   100   1            
2 13        Gisela Martínez   Meio do Funil Siqac rodado   100   1            
3 13        Manuela Pinho     Meio do Funil Siqac rodado   100   1            
4 13        Silvério Sacadura Meio do Funil Siqac rodado   100   1            
5 13        Manuela Pinho     Meio do Funil Siqac rodado   100   2            
6 13        Carlos Oleiro     Meio do Funil Siqac rodado   100   1

*Até aqui conseguimos deixar a base com apenas seis variaveis.
Agora precisamos filtrar pelo status de AS - Assinada.
A variavel que tem o status é a variavel razao status da base vendas.
Vamos utilizar o "merge", no R, o termo "merge" refere-se a uma operação de combinação de dados de duas ou mais tabelas (data frames) em uma única tabela com base em colunas em comum.*

base equipes - Coordenador	Gerente

In [76]:
head(vendas)

regional codigo obra codigobloco nome bloco unidade vendedor           
1 VIVAZ SP 3131        01          TORRE 01   000003  Odilia Maciel      
2 VIVAZ SP 3131        01          TORRE 01   000009  Vivaldo Cachoeira  
3 VIVAZ SP 3131        01          TORRE 01   000101  Enia Alburquerque  
4 VIVAZ SP 3131        01          TORRE 01   000103  Gisela Martínez    
5 VIVAZ SP 3131        01          TORRE 01   000104  Abílio Canhão      
6 VIVAZ SP 3131        01          TORRE 01   000105  Quintiliano Moreyra
  empresa de vendas mes contabil data de contabilização do sap tipo            
1 VIVAZ VENDAS      9/2020       2020-09-24 15:27:03           Venda Lançamento
2 VIVAZ VENDAS      9/2020       2020-09-24 14:51:56           Venda Lançamento
3 VIVAZ VENDAS      9/2020       2020-10-01 15:53:01           Venda Lançamento
4 VIVAZ VENDAS      9/2020       2020-10-01 16:52:39           Venda Lançamento
5 VIVAZ VENDAS      10/2020      2020-10-23 05:57:41           Venda Lançamento
6 VIVAZ VENDAS      9/2020       2020-09-24 06:47:27           Venda Lançamento
  tipo venda razao status           
1 Nova Venda AG - Suporte Financeiro
2 Nova Venda AG - Suporte Financeiro
3 Nova Venda AG - Suporte Financeiro
4 Nova Venda AG - Suporte Financeiro
5 Nova Venda AS - Assinada          
6 Nova Venda AS - Assinada

In [79]:
# Vamos fazer o merge e criar a nova base "nova_base"
nova_base <- merge(result, vendas, by.x = "Nome Vendedor", by.y = "vendedor", all = TRUE)

# Mostrando a nova base com as informações agrupadas
head(nova_base)


Nome Vendedor Atividade Classificação Nome Atividade Score regional
1 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
2 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
3 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
4 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
5 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
6 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
  codigo obra codigobloco nome bloco unidade empresa de vendas mes contabil
1 5157        03          TORRE 03   000152  SELLING SP        9/2017      
2 8497        01          TORRE 01   000307  VIVAZ VENDAS      12/2020     
3 7836        02          TORRE 02   000048  VIVAZ VENDAS      8/2020      
4 3131        01          TORRE 01   000504  VIVAZ VENDAS      9/2020      
5 7804        01          TORRE A    000601  VIVAZ VENDAS      6/2020      
6 9804        02          TORRE 02   000508  VIVAZ VENDAS      2/2020      
  data de contabilização do sap tipo             tipo venda
1 2017-10-02 15:32:26           Venda Estoque    Nova Venda
2 2020-12-22 12:50:29           Venda Lançamento Nova Venda
3 2020-08-31 11:51:39           Venda Estoque    Nova Venda
4 2020-09-22 16:43:24           Venda Lançamento Nova Venda
5 2020-06-30 17:00:48           Venda Estoque    Nova Venda
6 2020-02-18 16:18:03           Venda Estoque    Nova Venda
  razao status           
1 AS - Assinada          
2 AS - Assinada          
3 AS - Assinada          
4 AG - Suporte Financeiro
5 AS - Assinada          
6 AS - Assinada

In [78]:
# Vamos filtrar as linhas que contêm "AS - Assinada" na coluna "razao status"
Ranking_Vendedor <- nova_base %>%
  filter(`razao status` == "AS - Assinada")

# Mostrando a nova base filtrada
head(Ranking_Vendedor)

Nome Vendedor Atividade Classificação Nome Atividade Score regional
1 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
2 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
3 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
4 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
5 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
6 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
  codigo obra codigobloco nome bloco unidade empresa de vendas mes contabil
1 5157        03          TORRE 03   000152  SELLING SP        9/2017      
2 8497        01          TORRE 01   000307  VIVAZ VENDAS      12/2020     
3 7836        02          TORRE 02   000048  VIVAZ VENDAS      8/2020      
4 7804        01          TORRE A    000601  VIVAZ VENDAS      6/2020      
5 9804        02          TORRE 02   000508  VIVAZ VENDAS      2/2020      
6 9831        01          TORRE 01   000304  VIVAZ VENDAS      11/2020     
  data de contabilização do sap tipo             tipo venda razao status 
1 2017-10-02 15:32:26           Venda Estoque    Nova Venda AS - Assinada
2 2020-12-22 12:50:29           Venda Lançamento Nova Venda AS - Assinada
3 2020-08-31 11:51:39           Venda Estoque    Nova Venda AS - Assinada
4 2020-06-30 17:00:48           Venda Estoque    Nova Venda AS - Assinada
5 2020-02-18 16:18:03           Venda Estoque    Nova Venda AS - Assinada
6 2020-12-01 13:12:55           Venda Lançamento Nova Venda AS - Assinada

# Ranking Vendedor

1. *Classificação de todos os vendedores do score mais alto para o mais baixo. Será considerado diferencial a aplicação de uma análise de curva ABC que demonstre o número e quem são os vendedores que deverão receber bônus e o número e quem são os vendedores que irão para o comitê de baixa performance.*

In [29]:
# Vamos ordenar os vendedores pelo score em ordem decrescente
ranking_ordenado <- Ranking_Vendedor %>%
  arrange(desc(Score))

head(ranking_ordenado)

Nome Vendedor Atividade Classificação Nome Atividade Score regional
1 Aarão Barrios 13        Meio do Funil Siqac rodado   100   VIVAZ SP
2 Aarão Barrios 13        Meio do Funil Siqac rodado   100   VIVAZ SP
3 Aarão Barrios 13        Meio do Funil Siqac rodado   100   VIVAZ SP
4 Aarão Barrios 13        Meio do Funil Siqac rodado   100   VIVAZ SP
5 Aarão Barrios 13        Meio do Funil Siqac rodado   100   VIVAZ SP
6 Aarão Barrios 13        Meio do Funil Siqac rodado   100   VIVAZ SP
  codigo obra codigobloco nome bloco unidade empresa de vendas mes contabil
1 5157        03          TORRE 03   000152  SELLING SP        9/2017      
2 8497        01          TORRE 01   000307  VIVAZ VENDAS      12/2020     
3 7836        02          TORRE 02   000048  VIVAZ VENDAS      8/2020      
4 7804        01          TORRE A    000601  VIVAZ VENDAS      6/2020      
5 9804        02          TORRE 02   000508  VIVAZ VENDAS      2/2020      
6 9831        01          TORRE 01   000304  VIVAZ VENDAS      11/2020     
  data de contabilização do sap tipo             tipo venda razao status 
1 2017-10-02 15:32:26           Venda Estoque    Nova Venda AS - Assinada
2 2020-12-22 12:50:29           Venda Lançamento Nova Venda AS - Assinada
3 2020-08-31 11:51:39           Venda Estoque    Nova Venda AS - Assinada
4 2020-06-30 17:00:48           Venda Estoque    Nova Venda AS - Assinada
5 2020-02-18 16:18:03           Venda Estoque    Nova Venda AS - Assinada
6 2020-12-01 13:12:55           Venda Lançamento Nova Venda AS - Assinada

In [30]:
str(ranking_ordenado)

'data.frame':	62613 obs. of  16 variables:
 $ Nome Vendedor                : chr  "Aarão Barrios" "Aarão Barrios" "Aarão Barrios" "Aarão Barrios" ...
 $ Atividade                    : num  13 13 13 13 13 13 13 13 13 13 ...
 $ Classificação                : chr  "Meio do Funil" "Meio do Funil" "Meio do Funil" "Meio do Funil" ...
 $ Nome Atividade               : chr  "Siqac rodado" "Siqac rodado" "Siqac rodado" "Siqac rodado" ...
 $ Score                        : num  100 100 100 100 100 100 100 100 100 100 ...
 $ regional                     : chr  "VIVAZ SP" "VIVAZ SP" "VIVAZ SP" "VIVAZ SP" ...
 $ codigo obra                  : chr  "5157" "8497" "7836" "7804" ...
 $ codigobloco                  : chr  "03" "01" "02" "01" ...
 $ nome bloco                   : chr  "TORRE 03" "TORRE 01" "TORRE 02" "TORRE A" ...
 $ unidade                      : chr  "000152" "000307" "000048" "000601" ...
 $ empresa de vendas            : chr  "SELLING SP" "VIVAZ VENDAS" "VIVAZ VENDAS" "VIVAZ VENDAS" .

In [31]:
# Vamos remover as variáveis indesejadas
ranking_ordenado <- ranking_ordenado %>%
  select(-regional, -`codigo obra`, -codigobloco, -`nome bloco`, -unidade, -`empresa de vendas`)


In [32]:
# Vamos extrair apenas a parte da data (ignorando a hora) da coluna "data de contabilização do sap"
ranking_ordenado <- ranking_ordenado %>%
  mutate(`data de contabilização do sap` = as.Date(`data de contabilização do sap`))

In [33]:
# Vamos converter a coluna "mes contabil" para o formato Date
ranking_ordenado <- ranking_ordenado %>%
  mutate(`mes contabil` = as.Date(paste0(`mes contabil`, "/01"), format = "%m/%Y/%d"))

*Classificação de todos os vendedores do score mais alto para o mais baixo*

In [48]:
# Mostrando a nova base "ranking_ordenado" sem as variáveis removidas e já ordenada
head(ranking_ordenado)

Nome Vendedor Atividade Classificação Nome Atividade Score mes contabil
1 Aarão Barrios 13        Meio do Funil Siqac rodado   100   2017-09-01  
2 Aarão Barrios 13        Meio do Funil Siqac rodado   100   2020-12-01  
3 Aarão Barrios 13        Meio do Funil Siqac rodado   100   2020-08-01  
4 Aarão Barrios 13        Meio do Funil Siqac rodado   100   2020-06-01  
5 Aarão Barrios 13        Meio do Funil Siqac rodado   100   2020-02-01  
6 Aarão Barrios 13        Meio do Funil Siqac rodado   100   2020-11-01  
  data de contabilização do sap tipo             tipo venda razao status 
1 2017-10-02                    Venda Estoque    Nova Venda AS - Assinada
2 2020-12-22                    Venda Lançamento Nova Venda AS - Assinada
3 2020-08-31                    Venda Estoque    Nova Venda AS - Assinada
4 2020-06-30                    Venda Estoque    Nova Venda AS - Assinada
5 2020-02-18                    Venda Estoque    Nova Venda AS - Assinada
6 2020-12-01                    Venda Lançamento Nova Venda AS - Assinada

In [35]:
# Calculando o total de vendedores
total_vendedores <- nrow(ranking_ordenado)

In [36]:
# Calculando o número de vendedores que deverão receber bônus (por exemplo, os 20% melhores)
num_bonus <- round(total_vendedores * 0.2)

In [37]:
# Selecionando os vendedores que deverão receber bônus
vendedores_bonus <- ranking_ordenado %>%
  top_n(num_bonus, Score)


In [38]:
# Selecionando os vendedores que irão para o comitê de baixa performance (por exemplo, os 10% piores)
num_comite_baixa_perf <- round(total_vendedores * 0.1)

vendedores_comite_baixa_perf <- ranking_ordenado %>%
  tail(num_comite_baixa_perf)

In [39]:
# Mostrando os vendedores que deverão receber bônus em forma de tabela
cat("Vendedores que deverão receber bônus:\n")
kable(vendedores_bonus)


Vendedores que deverão receber bônus:




|Nome Vendedor       | Atividade|Classificação   |Nome Atividade   | Score|mes contabil |data de contabilização do sap |tipo             |tipo venda |razao status  |
|:-------------------|---------:|:---------------|:----------------|-----:|:------------|:-----------------------------|:----------------|:----------|:-------------|
|Aarão Barrios       |        13|Meio do Funil   |Siqac rodado     |   100|2017-09-01   |2017-10-02                    |Venda Estoque    |Nova Venda |AS - Assinada |
|Aarão Barrios       |        13|Meio do Funil   |Siqac rodado     |   100|2020-12-01   |2020-12-22                    |Venda Lançamento |Nova Venda |AS - Assinada |
|Aarão Barrios       |        13|Meio do Funil   |Siqac rodado     |   100|2020-08-01   |2020-08-31                    |Venda Estoque    |Nova Venda |AS - Assinada |
|Aarão Barrios       |        13|Meio do Funil   |Siqac rodado     |   100|2020-06-01   |2020-06-30                    |Venda Estoque    |Nova Venda |AS - Assinada |
|A

In [40]:
# Mostrando os vendedores que irão para o comitê de baixa performance em forma de tabela
cat("\nVendedores que irão para o comitê de baixa performance:\n")
kable(vendedores_comite_baixa_perf)


Vendedores que irão para o comitê de baixa performance:




|      |Nome Vendedor       | Atividade|Classificação |Nome Atividade    | Score|mes contabil |data de contabilização do sap |tipo             |tipo venda |razao status  |
|:-----|:-------------------|---------:|:-------------|:-----------------|-----:|:------------|:-----------------------------|:----------------|:----------|:-------------|
|56353 |Celestina Arantes   |         7|Lead Recebido |Espontânea        |   -10|2020-08-01   |2020-08-27                    |Venda Estoque    |Nova Venda |AS - Assinada |
|56354 |Celestina Arantes   |         7|Lead Recebido |Espontânea        |   -10|2020-07-01   |2020-07-21                    |Venda Estoque    |Nova Venda |AS - Assinada |
|56355 |Celestina Arantes   |         7|Lead Recebido |Espontânea        |   -10|2020-10-01   |2020-10-22                    |Venda Lançamento |Nova Venda |AS - Assinada |
|56356 |Celestina Arantes   |         7|Lead Recebido |Espontânea        |   -10|2020-07-01   |2020-07-24                    |Venda Estoqu

#Ranking Coordenador
2. *Classificação de todos os coordenadores, através da composição do score de sua equipe. Dica: Se atente para a diferença no número de vendedores das equipes. Não realize apenas a soma do score dos vendedores.*

In [89]:
# Fazendo o left_join para trazer o nome dos Coordenadores e Gerentes
Ranking_Vendedor2 <- left_join(Ranking_Vendedor, equipes, by = c("Nome Vendedor" = "Vendedor"))

# Mostrando a nova base após o left_join
head(Ranking_Vendedor2)

Nome Vendedor Atividade Classificação Nome Atividade Score regional
1 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
2 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
3 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
4 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
5 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
6 Aarão Barrios 7         Lead Recebido Espontânea     -10   VIVAZ SP
  codigo obra codigobloco nome bloco unidade empresa de vendas mes contabil
1 5157        03          TORRE 03   000152  SELLING SP        9/2017      
2 8497        01          TORRE 01   000307  VIVAZ VENDAS      12/2020     
3 7836        02          TORRE 02   000048  VIVAZ VENDAS      8/2020      
4 7804        01          TORRE A    000601  VIVAZ VENDAS      6/2020      
5 9804        02          TORRE 02   000508  VIVAZ VENDAS      2/2020      
6 9831        01          TORRE 01   000304  VIVAZ VENDAS      11/2020     
  data de contabilização do sap tipo             tipo venda razao status 
1 2017-10-02 15:32:26           Venda Estoque    Nova Venda AS - Assinada
2 2020-12-22 12:50:29           Venda Lançamento Nova Venda AS - Assinada
3 2020-08-31 11:51:39           Venda Estoque    Nova Venda AS - Assinada
4 2020-06-30 17:00:48           Venda Estoque    Nova Venda AS - Assinada
5 2020-02-18 16:18:03           Venda Estoque    Nova Venda AS - Assinada
6 2020-12-01 13:12:55           Venda Lançamento Nova Venda AS - Assinada
  Código Coordenador       Gerente       
1 1      Anacleto Parreira Oriana Camargo
2 1      Anacleto Parreira Oriana Camargo
3 1      Anacleto Parreira Oriana Camargo
4 1      Anacleto Parreira Oriana Camargo
5 1      Anacleto Parreira Oriana Camargo
6 1      Anacleto Parreira Oriana Camargo

*Primeiro vamos entender quantos vendedores temos por coordenador e quantos coordenadores por gerentes.*

In [98]:
# Calculando o número de vendedores distintos para cada coordenador
vendedores_distintos_coordenador <- Ranking_Vendedor2 %>%
  group_by(Coordenador) %>%
  summarise(Numero_Vendedores_Distintos = n_distinct(`Nome Vendedor`))

# Calculando o número de coordenadores distintos para cada gerente
coordenadores_distintos_gerente <- Ranking_Vendedor2 %>%
  group_by(Gerente) %>%
  summarise(Numero_Cordenadores_Distintos = n_distinct(Coordenador))

# Mostrando o resultado em formato de tabela
print("Vendedores Distintos por Coordenador:")
print(vendedores_distintos_coordenador)

print("Vendedores Distintos por Gerente:")
print(coordenadores_distintos_gerente)

[1] "Vendedores Distintos por Coordenador:"
# A tibble: 10 × 2
   Coordenador        Numero_Vendedores_Distintos
   <chr>                                    <int>
 1 Anacleto Parreira                            3
 2 Augusto Conde                                2
 3 Catarino Veiga                               7
 4 Clarindo Moniz                               6
 5 Cássio Lameirinhas                           7
 6 Fernando Ipanema                            13
 7 Firmina Sabala                               3
 8 Florêncio Quintal                            8
 9 Vasco Villalobos                             8
10 Íris Junqueira                               2
[1] "Vendedores Distintos por Gerente:"
# A tibble: 4 × 2
  Gerente            Numero_Cordenadores_Distintos
  <chr>                                      <int>
1 Oriana Camargo                                 5
2 Sidónio Thomé                                  2
3 Tabalipa Baião                                 4
4 Viridiano Medeiros    

In [90]:
# Calculando a pontuação agregada de cada equipe coordenada por um coordenador
pontuacao_equipes <- Ranking_Vendedor2 %>%
  group_by(Coordenador) %>%
  summarise(Pontuacao_Equipe = sum(Score))

# Classificando os coordenadores com base na pontuação agregada de suas equipes
classificacao_coordenadores <- pontuacao_equipes %>%
  arrange(desc(Pontuacao_Equipe))

# Mostrando a classificação dos coordenadores em formato de tabela
print(classificacao_coordenadores)

# A tibble: 10 × 2
   Coordenador        Pontuacao_Equipe
   <chr>                         <dbl>
 1 Fernando Ipanema            150514 
 2 Catarino Veiga              120247.
 3 Cássio Lameirinhas           79737.
 4 Florêncio Quintal            34570.
 5 Íris Junqueira               31225 
 6 Vasco Villalobos             28349.
 7 Firmina Sabala               26049.
 8 Anacleto Parreira            23879.
 9 Augusto Conde                23167 
10 Clarindo Moniz               17223.


In [91]:
# Calculando a pontuação agregada ponderada de cada equipe coordenada por um coordenador
pontuacao_equipes <- Ranking_Vendedor2 %>%
  group_by(Coordenador) %>%
  summarise(Pontuacao_Equipe = sum(Score * (1/n())))

# Classificando os coordenadores com base na pontuação agregada ponderada de suas equipes
classificacao_coordenadores <- pontuacao_equipes %>%
  arrange(desc(Pontuacao_Equipe))

# Mostrando a classificação dos coordenadores em formato de tabela
print(classificacao_coordenadores)

# A tibble: 10 × 2
   Coordenador        Pontuacao_Equipe
   <chr>                         <dbl>
 1 Firmina Sabala                18.2 
 2 Íris Junqueira                11.1 
 3 Florêncio Quintal             10.2 
 4 Catarino Veiga                 9.49
 5 Fernando Ipanema               9.16
 6 Augusto Conde                  8.47
 7 Vasco Villalobos               7.54
 8 Cássio Lameirinhas             7.37
 9 Anacleto Parreira              5.23
10 Clarindo Moniz                 4.30
